# CSCI 6390: Assignment 8
## Due November 22nd
### By: Nicholas Lutrzykowski 
The goal of this assignment is to implement EM and K-Means clustering algorithms.

In [2]:
# Import Statements 
import numpy as np
import matplotlib.pyplot as plt
from scipy.special import softmax
from scipy.special import logsumexp
from scipy.stats import multivariate_normal
import pandas as pd

### Import and setup data 

In [3]:
def read_data(filename):

    df = pd.read_csv(filename)
    
    df.drop([486, 5063])
    #df.drop(columns=[ ])
    data = pd.DataFrame(df).to_numpy()
    
    label = data[:,0].tolist()
    
    data = np.concatenate((data[:486, :], data[487:5063, :], data[5064:, :]), axis=0)
    data = data[:, 5:].astype(float)
    
    
    return data, label

In [4]:
data, label = read_data('codon_usage.csv')

C:\Users\lutrzn\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.8_qbz5n2kfra8p0\LocalCache\local-packages\Python38\site-packages\IPython\core\interactiveshell.py:3191: DtypeWarning: Columns (5,6) have mixed types.Specify dtype option on import or set low_memory=False.
  if await self.run_code(code, result, async_=asy):


In [5]:
def get_C(C_temp):
    C = np.zeros((len(C_temp),))
    words = ['arc', 'vrl', 'bct', 'plm', 'inv', 'vrt', 'mam', 'pln', 'rod', 'pri', 'phg']
    for i in range(len(C_temp)):
        for j in range(len(words)): 
            if C_temp[i] == words[j]:
                C[i] = j
                break
    return C

In [85]:
def get_prob(C):
    pci = np.zeros((int(np.amax(C))+1,))
    for i in range(pci.shape[0]):
        pci[i] = np.count_nonzero(C == i) / C.shape[0]

    return pci

In [1]:
def NMI_K_means(C_temp, T, C_index):
    C = get_C(C_temp)
    print(C)
    pc = get_prob(C)
    H_C = 0
    for i in range(pc.shape[0]):
        H_C += pc[i]*np.log(pc[i])
    
    H_T = 0
    pt = np.zeros((len(T),))
    for i in range(len(T)):
        pti = len(T[i]) / C.shape[0]
        H_T += pti*np.log(pti)
    
    H_T *= -1
    H_C *= -1
    r, k = pc.shape[0], pt.shape[0]
    
    H_T_C = 0
    for i in range(r):
        for j in range(k):
            pij = np.intersect1d(np.where(C == i), C_index[j]).shape[0] / C.shape[0]
            if pij == 0:
                continue
            else:
                H_T_C += pij * np.log(pij/pc[i])
    H_T_C *= -1
    I_C_T = H_T - H_T_C
    
    NMI = I_C_T / np.sqrt(H_C*H_T)
    
    return NMI

In [87]:
def NMI2(C_temp, T):
    C = get_C(C_temp)
    
    pc = get_prob(C)
    H_C = 0
    for i in range(pc.shape[0]):
        H_C += pc[i]*np.log(pc[i])
    
    H_T = 0
    pt = np.zeros((np.amax(T)+1,))
    
    for i in range(pt.shape[0]):
        pti = np.count_nonzero(T==i) / C.shape[0]
        if pti == 0: 
            continue 
        else:
            H_T += pti*np.log(pti)
    
    H_T *= -1
    H_C *= -1
    
    r, k = pc.shape[0], pt.shape[0]
    
    H_T_C = 0
    for i in range(r):
        for j in range(k):
            pij = np.intersect1d(np.where(C == i), np.where(T == i)).shape[0] / C.shape[0]
            if pij == 0:
                continue
            else:
                H_T_C += pij * np.log(pij/pc[i])
    H_T_C *= -1
    I_C_T = H_T - H_T_C
    
    NMI = I_C_T / np.sqrt(H_C*H_T)
    
    return NMI

### Expectation Maximization Clustering

In [88]:
def expectation_max(D, k, epsilon):
    # Initialize covalance and weight matrices
    rand_index = np.random.choice(D.shape[0], k)
    mu = np.take(D, rand_index, axis=0)
    cov = np.ones((k, D.shape[1], D.shape[1]))*np.identity(D.shape[1])
    prob = np.ones((k,))*(1/k)
    dif = np.sum(np.ones((k, D.shape[1]))*epsilon*2)
    
    w = np.zeros((data.shape[0], k))
    w_prime = np.log(np.ones((data.shape[0], k))*1e-7)
    
    min_indices = np.argmin(np.linalg.norm((data[:,None] - mu), axis=2), axis=1)
    w_prime[np.arange(w_prime.shape[0]), min_indices] = np.log(1)
    prob = np.log(np.count_nonzero(w_prime==0, axis=0)/data.shape[0])
    w_prime = w_prime + prob
    
    log_sum = logsumexp(w_prime, axis=1)
    for i in range(k):
        for j in range(data.shape[0]):
            w[j, i] = np.exp(w_prime[j, i] - log_sum[j])
    
    for i in range(k):
        cov[i,:,:] = np.matmul(np.multiply(data.T, w[:, i]), data) / np.sum(w[:,i])
    
    i = 0
    while dif > epsilon: 
        
        # Get posterior probability
        for i in range(k):
            w[:, i] = multivariate_normal.logpdf(D, mu[i,:], cov[i,:,:], allow_singular=True)*prob[i]
            
        total = np.sum(w, axis=1)
        for i in range(k):
            w[:, i] = w[:,i] / total
        
        # Maximization step
        mu_prev = mu 
        for i in range(k):
            temp = mu[i,:]
            mu[i,:] = np.matmul(w[:, i].T, data) / np.sum(w[:,i])
            
            dif = data - mu[i,:]
            cov[i,:,:] = np.matmul(np.multiply(data.T, w[:, i]), data) / np.sum(w[:,i])
        
        min_indices = np.argmin(np.linalg.norm((data[:,None] - mu), axis=2), axis=1)
        w_prime[np.arange(w_prime.shape[0]), min_indices] = np.log(1)
        prob = np.log(np.count_nonzero(w_prime==0, axis=0)/data.shape[0])
        w_prime = w_prime + prob
        
        dif = np.linalg.norm(mu_prev-mu)
        
    

    return mu, cov, min_indices

In [103]:
k = 11

max_NMI = 0 
mu_opt, cov_opt, indices_opt, cluster_sizes_opt = 0, 0, 0, 0
for i in range(10):
    mu, cov, indices = expectation_max(data, k, 0.001)
    cluster_sizes = np.zeros((k,))
    for i in range(k): 
        cluster_sizes[i] = np.count_nonzero(indices == i)
    NMI = NMI2(label, indices)
    
    if NMI > max_NMI:
        mu_opt, cov_opt, indices_opt, max_NMI, cluster_sizes_opt = mu, cov, indices, NMI, cluster_sizes
    

np.set_printoptions(suppress = True)
print("The mu values are:", mu_opt)
print("The cov matrixes are:", cov_opt)
print("The cluster sizes are:", cluster_sizes_opt)
print("NMI is:", max_NMI)


C:\Users\lutrzn\AppData\Local\Temp\ipykernel_34960\1405650103.py:47: RuntimeWarning: divide by zero encountered in log
  prob = np.log(np.count_nonzero(w_prime==0, axis=0)/data.shape[0])


The mu values are: [[ 0.02569459  0.03639685  0.02949597  0.00411851  0.02381651  0.03410454
   0.06122217  0.0145698   0.03764102  0.04348094  0.03377972  0.01112115
   0.0113555   0.01411557  0.01921393  0.00763727  0.01417527  0.03523792
   0.02342562  0.00733462  0.01092598  0.02012007  0.02324508  0.00483675
   0.00374953  0.00871791  0.02102184  0.02218889  0.00994494  0.01135166
   0.01879514  0.02257011  0.00337304  0.00275448  0.00889566  0.0143639
   0.03092909  0.03173457  0.0037697   0.01273984  0.01761484  0.01944563
   0.00411324  0.01202818  0.02567484  0.00196979  0.00468996  0.00711544
   0.01768421  0.0196911   0.00264916  0.00243851  0.00736001  0.01007183
   0.00351527  0.00046068 -0.00043579  0.00526505  0.01515549  0.01571372
   0.00556226  0.00234343  0.00062169  0.02528375]
 [ 0.02935234  0.03664593  0.03480739  0.00438466  0.02632155  0.03267435
   0.07124618  0.00556098  0.04337393  0.04403331  0.04174833  0.00983273
   0.01217505  0.00971217  0.02219835  0.00

### K-Means Clustering

In [7]:
def K_means(D, k, epsilon):
    # Initialize mu
    rand_index = np.random.choice(D.shape[0], k)
    mu_prev = np.take(D, rand_index, axis=0)
    mu = np.zeros(mu_prev.shape)
    
    # Initializations for end-condition variables
    t = 0 
    dif = np.sum(np.ones((k, D.shape[1]))*epsilon*2)
    res = [] 
    
    while dif > epsilon: 
        t = t + 1
        C = [ [] for _ in range(k) ]
        C_index = [ [] for _ in range(k) ]
        
        counter = 0
        for x in D: 
            i = np.argmin(np.linalg.norm(mu_prev-x, axis=1))
            C[i].append(x)
            C_index[i].append(counter)
            counter += 1
            
        
        for i in range(k):
            if len(C[i]) > 0:
                mu[i] = 1/len(C[i])*np.sum(np.array(C[i]), axis=0)
        
        
        dif = np.sum(np.linalg.norm(mu_prev-mu, axis=1))
        mu_prev = mu
        mu = np.zeros(mu_prev.shape)
        
        if dif <= epsilon: res = C
        
    
    return mu_prev, C, C_index

In [8]:
k = 11

mu_opt, C_opt, C_index_opt, NMI_opt, cluster_sizes_opt = 0, 0, 0, 0, 0
for i in range(1):
    mu, C, C_index = K_means(data, k, 0.001)

    cluster_sizes = np.zeros((k,))
    for i in range(len(C)):
        cluster_sizes[i] = len(C[i])
    
    print(C)
    print(C_index)
    nmi = NMI_K_means(label, C, C_index)
    
    if nmi > NMI_opt: 
        mu_opt, C_opt, C_index_opt, NMI_opt, cluster_sizes_opt = mu, C, C_index, nmi, cluster_sizes
    

print("The cluster sizes are:")
print(cluster_sizes_opt)
print("The cluster means are:")
print(mu_opt)
print("The NMMI for K-means clustering is:")
print(NMI_opt)

[[array([0.01654, 0.01203, 0.0005 , 0.00351, 0.01203, 0.03208, 0.001  ,
       0.0401 , 0.00551, 0.02005, 0.00752, 0.02506, 0.01103, 0.0411 ,
       0.00902, 0.03308, 0.01003, 0.05013, 0.01554, 0.01103, 0.02356,
       0.03208, 0.01203, 0.00501, 0.01003, 0.01203, 0.03158, 0.01905,
       0.02456, 0.01353, 0.02155, 0.00251, 0.00652, 0.0015 , 0.01554,
       0.00501, 0.02105, 0.00902, 0.01053, 0.00501, 0.02256, 0.00301,
       0.03108, 0.00401, 0.02607, 0.00251, 0.01153, 0.00501, 0.02356,
       0.01053, 0.0386 , 0.00401, 0.00702, 0.00401, 0.00451, 0.01303,
       0.03559, 0.01003, 0.04612, 0.01203, 0.04361, 0.00251, 0.0005 ,
       0.     ]), array([0.02714, 0.01357, 0.00068, 0.00678, 0.00407, 0.02849, 0.00204,
       0.0441 , 0.01153, 0.0251 , 0.00882, 0.03324, 0.00814, 0.04071,
       0.00814, 0.03256, 0.01085, 0.04885, 0.01221, 0.01357, 0.00678,
       0.02714, 0.01221, 0.00407, 0.01425, 0.01221, 0.01967, 0.02239,
       0.01289, 0.02103, 0.01493, 0.00407, 0.00475, 0.00068, 0.02035,


NameError: name 'get_prob' is not defined